In [1]:
import pandas as pd
import numpy as np

import matplotlib.pyplot as plt
import plotly.express as px
import seaborn as sns
import folium as fl
from folium.plugins import HeatMap

import plotly.express as px

import glob

from processing.parsing import *

In [2]:
# Idea:
# Más adelante, agrupar las columnas desechadas en una sola para crear una sola llamada 'Descripción'
# y hacer un Cluster con NLP con ella

In [34]:
import csv
import ast
import re

############### MUY IMPORTANTE, PANDAS NO CONSIGUE LEER LOS CSV BIEN, ASI QUE TENEMOS QUE PARSEARLOS MANUALMENTE

with open('../scraping/data/almeria.csv', encoding = 'utf-8') as file:
    data = file.readlines()
    
    pattern_dict = r'\{([^}]+)\}'
    pattern_list = r'\[([^]]+)\]'
    
    for row in data[1:]:
        match = re.findall(pattern_dict, row)
        if len(match) == 0:
            print(row)
            continue
        numeric_data = ast.literal_eval('{' + match[0] + '}')

        row_ = row[:- 4 -len(match[0])]

        row_ = row_.split(',')
        
        updated = row_.pop()
        agency = row_.pop()

        row_ = ','.join(row_)

        match = re.findall(pattern_list, row_)
        if len(match) == 0:
            print(row_)
            continue
        characteristics = ast.literal_eval('[' + match[0] + ']')

        row__ = row_[:- 4 -len(match[0])]

        row__ = row__.split(',')

        lng = row__.pop()
        lat = row__.pop()
        price = row__.pop(0)

        title_location = ','.join(row__)

        print(price, title_location, lat, lng, agency, updated)
        print(characteristics, numeric_data)




42.000 € Piso en venta en Calle Alfarerías, nº SN,Calle Alfarerías, nº SN. Alhama de Almería 36.959564 -2.57303 Inmuebles de Servihabitat Servicios Inmobiliarios 1674860940.0
['Superficie construida : 118 m²', 'Superficie útil : 84 m²', 'Habitaciones : 2', 'Baños : 2', 'Antigüedad : Entre 10 y 20 años', 'Referencia : SH1-60573269', 'Cocina', 'Ascensor : 2', 'Piscina : Comunitario', 'Clasificación:  Disponible', 'Emisiones:  28,11 Kg CO2/m2 año  A B C D E F G'] {'timestamp': '1698612697314815', 'soft_url': 'piso_alhama_de_almeria_centro_urbano_95915115014_102500_'}
27.000 € Casa rústica en venta en Calle Colon, 3,Calle Colon, 3. Rágol 36.9948 -2.6807 Inmuebles de FINCAS ALPUJARRA.COM 1674774600.0
['Superficie construida : 102 m²', 'Superficie útil : 95 m²', 'Habitaciones : 4', 'Baños : 1', 'Tipo de casa : Rústica', 'Conservación : En buen estado', 'Referencia : SA4409-307. - RÁGOL CASA -C/ COLON', 'Chimenea : No', 'Terraza', 'Orientación : Sur', 'Clasificación:  En trámite', 'Pedir más 

In [12]:
data

['price,title,province,location,lat,lng,characteristics,agency,updated,numeric_data\n',
 "42.000 €,Piso en venta en Calle Alfarerías, nº SN,Calle Alfarerías, nº SN. Alhama de Almería,36.959564,-2.573037,['Superficie construida : 118 m²', 'Superficie útil : 84 m²', 'Habitaciones : 2', 'Baños : 2', 'Antigüedad : Entre 10 y 20 años', 'Referencia : SH1-60573269', 'Cocina', 'Ascensor : 2', 'Piscina : Comunitario', 'Clasificación:  Disponible', 'Emisiones:  28,11 Kg CO2/m2 año  A B C D E F G'],Inmuebles de Servihabitat Servicios Inmobiliarios,1674860940.0,{'timestamp': '1698612697314815', 'soft_url': 'piso_alhama_de_almeria_centro_urbano_95915115014_102500_'}\n",
 "27.000 €,Casa rústica en venta en Calle Colon, 3,Calle Colon, 3. Rágol,36.9948,-2.68074,['Superficie construida : 102 m²', 'Superficie útil : 95 m²', 'Habitaciones : 4', 'Baños : 1', 'Tipo de casa : Rústica', 'Conservación : En buen estado', 'Referencia : SA4409-307. - RÁGOL CASA -C/ COLON', 'Chimenea : No', 'Terraza', 'Orientació

In [7]:
df = pd.read_csv('../scraping/data/almeria.csv')
# df = [pd.read_csv(x) for x in glob.glob('../scraping/data/*.csv')]
df

ParserError: Error tokenizing data. C error: Expected 23 fields in line 7, saw 27


In [ ]:
df

['../scraping/data\\almeria.csv',
 '../scraping/data\\asturias.csv',
 '../scraping/data\\cantabria.csv',
 '../scraping/data\\gijon_concejo_xixon_conceyu_gijon.csv',
 '../scraping/data\\girona.csv',
 '../scraping/data\\guipuzcoa_gipuzkoa.csv',
 '../scraping/data\\lleida.csv',
 '../scraping/data\\lugo.csv',
 '../scraping/data\\navarra_nafarroa.csv',
 '../scraping/data\\ourense.csv',
 '../scraping/data\\pontevedra.csv',
 '../scraping/data\\tarragona.csv',
 '../scraping/data\\vizcaya_bizkaia.csv']

In [53]:
fig = px.bar([df[x].dropna().count() for x in df.columns],
             y = df.columns,
             x = [df[x].dropna().count() for x in df.columns])

fig.update_layout(height = 1000)

In [54]:
# Lista de columnas a revisar para decidir cómo tratar la información para entrenar el modelo en el futuro
scratched_features_col = ['Cocina', 'Cocina equipada', 'Superficie solar', 'Sistema de seguridad', 'Portero automático',
                      'Aire acondicionado', 'Puerta blindada', 'Amueblado', 'Trastero', 'Calefacción', 'Gas',
                      'Tipo de casa', 'Piscina', 'Vidrios dobles', 'Planta', 'Tipo suelo', 'Balcón', 'Orientación',
                      'Armarios empotrados', 'Comedor']

# Cocina -> hacerla categórica (americana, independiente, amueblada, sin amueblar)
# Cocina equipada -> revisarla con 'Cocina'
# Superficie solar -> Seguramente sea interesante solo para chalets
# Sistema de seguridad -> hacerla categórica (conserje, alarma, videovigilancia, etc.) mezclándola con 'Portero automático'
# Portero automático -> relacionar con 'Sistema de seguridad'
# Aire acondicionado -> hacerla categórica numérica
# Puerta blindada -> hacerla binaria
# Amueblado -> hacerla categórica (sí, no, parcial)
# Trastero -> hacerla categórica (sí, no, comunitario)
# Calefacción -> hacerla categórica (gas natural, butano, eléctrico, frío-calor, chimenea, no)
# Gas -> hacerla categórica (revisar Calefacción)
# Tipo de casa -> hacerla categórica ('Adosada', 'Pareada', ' Rústica', ' Unifamiliar', 'otro)
# Piscina -> hacerla categórica (privada, comunitaria, opcional-comunitaria, no, etc)
# Vidrios dobles -> hacerla categórica (corredera, oscilobatiente, abrir-cerrar, doble aluminio, no)
# Planta -> hacerla categórica numérica (-2, -1, 0, 1, 2, etc)
# Tipo suelo -> hacerla binaria (frío, caliente)
# Balcón -> hacerla categórica numérica
# Armarios empotrados -> hacerla binaria
# Comedor -> hacerla categórica

In [55]:
features_col = ['price', 'title', 'lat', 'lng', 'location', 'Habitaciones', 'Superficie construida',
                'Jardín', 'Gastos de comunidad', 'Antigüedad', 'Baños', 'Superficie útil', 'Ascensor',
                'Garaje', 'Conservación', 'agency', 'updated']

# Garaje -> hacer varias columnas columnas (tien o no tiene, cantidad, metros cuadrados)
# location -> sacar columnas (tipo de vía, locación, etc)
# title -> revisar con columna 'Tipo de casa' para obtener una columna con tipo de vivienda

In [56]:
df_features = df[features_col]

In [57]:
# Sería interesante poner una columna que tenga la fecha actual? Para que el modelo compare con la fecha de publicación

In [58]:
df_ = getType(df_features)


c:\Users\cuicuidev\Desktop\pisoscom\ml\processing\parsing.py:97: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [59]:
df_ = getStreetType(df_)

c:\Users\cuicuidev\Desktop\pisoscom\ml\processing\parsing.py:125: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [60]:
streets = df_['street'].dropna().unique()

In [61]:
unique_streets = []

for street in streets:
    for s in street.split():
        if s == 'c' or s == 'av':
            continue
        unique_streets.append(s)

unique_streets = list(set(unique_streets))

In [62]:
unique_streets_en = {'calle' : 'street', 'bulevar' : 'boulevard', 'plaza' : 'square', 'autovía' : 'highway', 'carretera' : 'road', 'parque' : 'park', 'paseo' : 'walk', 'avenida' : 'avenue'}
unique_streets

['bulevar',
 'paseo',
 'carretera',
 'parque',
 'calle',
 'autovia',
 'avenida',
 'plaza']

In [63]:
for street in unique_streets:
    df_[street] = df_['street'].apply(lambda x: 0 if pd.isna(x) else sum([1 for _ in x.split() if 'calle' in x]))

df_ = df_.drop('street', axis = 1)

C:\Users\cuicuidev\AppData\Local\Temp\ipykernel_13204\917673754.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\cuicuidev\AppData\Local\Temp\ipykernel_13204\917673754.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\cuicuidev\AppData\Local\Temp\ipykernel_13204\917673754.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.

In [64]:
df_

price                                              title        lat  \
0      176000.0  Apartamento en venta en Abantos-Monte Carmelo-...  40.593445   
1      116500.0  Apartamento en venta en Calle de Ercilla, 20, ...  40.402079   
2      169000.0                    Apartamento en venta en Ajalvir  40.534457   
3      174000.0                   Apartamento en venta en Alcorcón  40.344358   
4      130000.0                   Apartamento en venta en Alcorcón  40.347096   
...         ...                                                ...        ...   
15841  135000.0        Piso en venta en Calle de la Circunvalación  40.454606   
15842  210000.0                    Piso en venta en Calle de Urano  40.441928   
15843  324600.0                           Piso en venta en Fresnos  40.448403   
15844  249900.0                  Piso en venta en Calle de Cibeles  40.444707   
15845  253800.0                           Piso en venta en Fresnos  40.447273   

            lng                                           location  \
0     -4.145386  Abantos-Monte Carmelo-El Rosario (San Lorenzo ...   
1     -3.702151  Calle de Ercilla, 20, cerca de Calle del Labra...   
2     -3.479415                                            Ajalvir   
3     -3.825283                           Casco Antiguo (Alcorcón)   
4     -3.827826                           Casco Antiguo (Alcorcón)   
...         ...                                                ...   
15841 -3.455234  Calle de la Circunvalación. Zona Suroeste (Tor...   
15842 -3.473036  Calle de Urano. Zona Suroeste (Torrejón de Ardoz)   
15843 -3.470899                  Zona Suroeste (Torrejón de Ardoz)   
15844 -3.473520  Calle de Cibeles. Zona Suroeste (Torrejón de A...   
15845 -3.473262                  Zona Suroeste (Torrejón de Ardoz)   

       Habitaciones Superficie construida        Jardín Gastos de comunidad  \
0               1.0                 63 m²   Comunitario      Entre 40 y 60€   
1               NaN                 25 m²           NaN                 NaN   
2               1.0                 70 m²           NaN                 NaN   
3               1.0                 60 m²           NaN                 NaN   
4               2.0                 60 m²           NaN      Entre 60 y 80€   
...             ...                   ...           ...                 ...   
15841           3.0                 67 m²           NaN                 NaN   
15842           1.0                 79 m²           NaN     Entre 80 y 100€   
15843           4.0                140 m²           NaN                 NaN   
15844           3.0                106 m²           NaN     Entre 80 y 100€   
15845           3.0                 90 m²           NaN                 NaN   

                Antigüedad  ...       updated         type bulevar paseo  \
0       Entre 10 y 20 años  ...  1.674861e+09  Apartamento       0     0   
1           Más de 50 años  ...  1.674947e+09  Apartamento       2     2   
2                      NaN  ...  1.673392e+09  Apartamento       0     0   
3                      NaN  ...  1.672960e+09  Apartamento       0     0   
4                      NaN  ...  1.672615e+09  Apartamento       0     0   
...                    ...  ...           ...          ...     ...   ...   
15841                  NaN  ...  1.672960e+09         Piso       1     1   
15842                  NaN  ...  1.672615e+09         Piso       1     1   
15843                  NaN  ...  1.672874e+09         Piso       0     0   
15844   Entre 20 y 30 años  ...  1.672874e+09         Piso       1     1   
15845                  NaN  ...  1.672701e+09         Piso       0     0   

      carretera parque  calle autovia  avenida  plaza  
0             0      0      0       0        0      0  
1             2      2      2       2        2      2  
2             0      0      0       0        0      0  
3             0      0      0       0        0      0  
4             0      0      0       0        0      0 

In [65]:
df_ = df_.drop('title', axis = 1)

In [66]:
df_ = df_.drop('location', axis = 1)

# Parsing de 'agency'

In [67]:
agency_col = df_['agency'].unique()

agencies = []
for agency in agency_col:
        
    if pd.isna(agency):
        continue
    if 'inmuebles' in agency.lower():
        agencies.append(agency)

len(agencies)

1325

In [68]:
df_['publisher'] = df_['agency'].apply(lambda x: 'particular' if x not in agencies else 'inmobiliaria')

In [69]:
df_ = df_.drop('agency', axis = 1)

# Parsing de 'Gastos de comunidad'

In [70]:
len(df_['Gastos de comunidad'].unique())

# CASOS
# 'Entre X y Y€'
# x,y
# x
# Más de x€
# x€
# x,y€
# nan, Gastos de comunidad, anual, trimestral/trimestre, 0, No, 
# x + y

360

In [71]:
# De momento quitamos esa columna
df_ = df_.drop('Gastos de comunidad', axis = 1)

# Parsing de 'Antigüedad'

In [72]:
df_['Antigüedad'].unique()

array([' Entre 10 y 20 años', ' Más de 50 años', nan,
       ' Entre 30 y 50 años', ' Entre 20 y 30 años', ' Entre 5 y 10 años',
       ' Menos de 5 años'], dtype=object)

In [73]:
antiguedad_col = df_['Antigüedad'].unique()
antiguedades = {' Menos de 5 años': 0,
                ' Entre 5 y 10 años' : 5,
                ' Entre 10 y 20 años' : 10,
                ' Entre 20 y 30 años' : 20,
                ' Entre 30 y 50 años' : 30,
                ' Más de 50 años': 50,}

In [74]:
df_['age'] = df_['Antigüedad'].replace(antiguedades)

In [75]:
df_ = df_.drop('Antigüedad', axis = 1)

# Parsing de 'Garaje'

In [76]:
df_['garage'] = df_['Garaje'].apply(lambda x: 'no' if pd.isna(x) else 'yes')

In [77]:
df_ = df_.drop('Garaje', axis = 1)

# Parsing de 'Ascensor'

In [78]:
# algunos pone 'no tiene'
df_['lift'] = df_['Ascensor'].apply(lambda x: 'no' if pd.isna(x) else 'yes')

In [79]:
df_ = df_.drop('Ascensor', axis = 1)

# Parsing de 'Superficie construida'

In [80]:
df_['surface'] = df_['Superficie construida'].apply(lambda x: np.nan if pd.isna(x) else int(''.join([_ for _ in x[:-3] if _.isnumeric()])))

In [81]:
df_ = df_.drop('Superficie construida', axis = 1)

# Parsing de 'Superficie útil'

In [82]:
df_['net_surface'] = df_['Superficie útil'].apply(lambda x: np.nan if pd.isna(x) else int(''.join([_ for _ in x[:-3] if _.isnumeric()])))

In [83]:
df_ = df_.drop('Superficie útil', axis = 1)


# Parsing de 'Jardín'

In [84]:
df_['garden'] = df_['Jardín'].apply(lambda x: 'no' if pd.isna(x) else 'yes')

In [85]:
df_ = df_.drop('Jardín', axis = 1)

# Renaming de columnas en español

In [86]:
df_['rooms'] = df_['Habitaciones']
df_['condition'] = df_['Conservación']
df_['bathrooms'] = df_['Baños']

df_ = df_.drop(['Habitaciones', 'Baños', 'Conservación'], axis = 1)

# Save

In [87]:
df_.to_csv('../data/madrid_preprocessed.csv', index = False)

# Read

In [88]:
df_ = pd.read_csv('../data/madrid_preprocessed.csv')
df_

price        lat       lng       updated         type  bulevar  \
0      176000.0  40.593445 -4.145386  1.674861e+09  Apartamento        0   
1      116500.0  40.402079 -3.702151  1.674947e+09  Apartamento        2   
2      169000.0  40.534457 -3.479415  1.673392e+09  Apartamento        0   
3      174000.0  40.344358 -3.825283  1.672960e+09  Apartamento        0   
4      130000.0  40.347096 -3.827826  1.672615e+09  Apartamento        0   
...         ...        ...       ...           ...          ...      ...   
15841  135000.0  40.454606 -3.455234  1.672960e+09         Piso        1   
15842  210000.0  40.441928 -3.473036  1.672615e+09         Piso        1   
15843  324600.0  40.448403 -3.470899  1.672874e+09         Piso        0   
15844  249900.0  40.444707 -3.473520  1.672874e+09         Piso        1   
15845  253800.0  40.447273 -3.473262  1.672701e+09         Piso        0   

       paseo  carretera  parque  calle  ...     publisher   age  garage lift  \
0          0          0       0      0  ...  inmobiliaria  10.0     yes  yes   
1          2          2       2      2  ...  inmobiliaria  50.0      no  yes   
2          0          0       0      0  ...  inmobiliaria   NaN      no  yes   
3          0          0       0      0  ...  inmobiliaria   NaN      no  yes   
4          0          0       0      0  ...  inmobiliaria   NaN      no  yes   
...      ...        ...     ...    ...  ...           ...   ...     ...  ...   
15841      1          1       1      1  ...  inmobiliaria   NaN      no  yes   
15842      1          1       1      1  ...  inmobiliaria   NaN     yes  yes   
15843      0          0       0      0  ...  inmobiliaria   NaN     yes  yes   
15844      1          1       1      1  ...  inmobiliaria  20.0     yes   no   
15845      0          0       0      0  ...  inmobiliaria   NaN     yes  yes   

       surface net_surface garden  rooms        condition bathrooms  
0         63.0        46.0    yes    1.0       A estrenar       1.0  
1         25.0         NaN     no    NaN              NaN       1.0  
2         70.0        67.0     no    1.0   En buen estado       1.0  
3         60.0        50.0     no    1.0              NaN       1.0  
4         60.0        54.0     no    2.0              NaN       1.0  
...        ...         ...    ...    ...              ...       ...  
15841     67.0        62.0     no    3.0       A reformar       1.0  
15842     79.0        63.0     no    1.0   En buen estado       2.0  
15843    140.0         NaN     no    4.0              NaN       3.0  
15844    106.0        96.0     no    3.0   En buen estado       2.0  
15845     90.0         NaN     no    3.0              NaN       2.0  

[15846 rows x 23 columns]

In [89]:
# Distribución de los precios para encontrar outliers
fig = px.histogram(data_frame=df_, x='price')
fig.show()

In [90]:
# Distribución de la cantidad de baños
fig = px.histogram(data_frame=df_, x='bathrooms')
fig.show()

In [91]:
# Distribución de la cantidad de baños
fig = px.histogram(data_frame=df_, x='surface')
fig.show()

In [92]:
# Distribución del número de habitaciones para encontrar outliers
fig = px.histogram(data_frame=df_, x='rooms')
fig.show()

In [93]:
# Distribución de la condición de las viviendas
fig = px.histogram(data_frame=df_, x='condition')
fig.show()

In [94]:
# Distribución del tipo de vivienda
fig = px.histogram(data_frame=df_, x='type')
fig.show()

In [95]:
# Distribución de los precios por número de habitaciones y por publisher
fig = px.box(df_.dropna(), x='rooms', y='price', facet_col='publisher')
fig.update_layout(title='Rooms vs Price by the publisher', xaxis_title='Nº of rooms', yaxis_title='Prices')
fig.show()

In [96]:
# Cantidad de publicaciones hechas por inmobiliarias vs particulares
fig = px.pie(df_, names='publisher', values=df_.index)
fig.update_traces(textinfo='percent+label')
fig.update_layout(title='Amount of advertisements by the publisher')
fig.show()

In [97]:
# Mapa de calor
heatmap_ = fl.Map(location=[36.9592884,-6.5695077], zoom_start=5)
HeatMap(df_[['lat', 'lng', 'price']].dropna()).add_to(heatmap_)
heatmap_

# heatmap_.save("heatmap_by_prices.html")

In [98]:
# # Mapa con todas las ubicaciones de las viviendas (quitando nans)
# # Cuesta ejecutarlo
# map = fl.Map(location=[36.9592884,-6.5695077], zoom_start=5)
# for loc in [(x, y) for x, y in zip(df_['lat'].dropna(), df_['lng'].dropna())]:
#     fl.Marker(loc).add_to(map)
# # map

# map.save("locations_map.html")